Les bibliothèques nécessaires pour la suite du code

In [2]:
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt
import seaborn as sns
import cv2

from tensorflow.keras import layers, models
from tensorflow.keras.preprocessing.image import ImageDataGenerator

from tensorflow.keras.preprocessing import image
from tensorflow.keras.models import load_model
import os
from tensorflow.keras.utils import img_to_array


Verifier les chemins d'accès au dataset 

In [ ]:

dataset_path = './fer2013'


ds_train = tf.keras.preprocessing.image_dataset_from_directory(
    dataset_path + "/train",
    image_size=(48, 48),
    batch_size=32,
    color_mode="grayscale",
    shuffle=True
)



Found 28709 files belonging to 7 classes.


In [4]:


ds_valid = tf.keras.preprocessing.image_dataset_from_directory(
    dataset_path + "/test",
    image_size=(48, 48),
    batch_size=32,
    color_mode="grayscale",
    shuffle=False
)



Found 7178 files belonging to 7 classes.


Premier test de CNN

In [ ]:


model = tf.keras.Sequential([
    # Bloc 1
    tf.keras.layers.Conv2D(64, (3,3), activation='relu', padding='same'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.Conv2D(64, (3,3), activation='relu', padding='same'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.MaxPooling2D(pool_size=(2,2)),
    tf.keras

.layers.Dropout(0.25),

    # Bloc 2
    tf.keras.layers.Conv2D(128, (3,3), activation='relu', padding='same'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.Conv2D(128, (3,3), activation='relu', padding='same'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.MaxPooling2D(pool_size=(2,2)),
    tf.keras.layers.Dropout(0.25),

    # Bloc 3
    tf.keras.layers.Conv2D(256, (3,3), activation='relu', padding='same'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.Conv2D(256, (3,3), activation='relu', padding='same'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.MaxPooling2D(pool_size=(2,2)),
    tf.keras.layers.Dropout(0.25),

    # Bloc 4


    tf.keras.layers.Conv2D(512, (3,3), activation='relu', padding='same'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.Conv2D(512, (3,3), activation='relu', padding='same'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.MaxPooling2D(pool_size=(2,2)),
    tf.keras.layers.Dropout(0.25),

    # Fully Connected Layers
    tf.keras.layers.Flatten(),
    tf.keras.layers.Dense(512, activation='relu'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.Dropout(0.5),
    tf.keras.layers.Dense(256, activation='relu'),
    tf.keras.layers.BatchNormalization(),
    tf.keras.layers.Dropout(0.5),
    
    # Output Layer
    tf.keras.layers.Dense(7, activation='softmax') 
])

In [ ]:

model.compile(loss="sparse_categorical_crossentropy", optimizer="adam", metrics=["accuracy"])
model.fit(ds_train, validation_data=ds_valid, epochs=15, callbacks=[tf.keras.callbacks.EarlyStopping(min_delta=0.001, monitor="val_loss", restore_best_weights=True, patience=20)], verbose=1)

Epoch 1/15
898/898 ━━━━━━━━━━━━━━━━━━━━ 233s 260ms/step - accuracy: 0.5568 - loss: 1.1789 - val_accuracy: 0.5678 - val_loss: 1.1392
Epoch 2/15
898/898 ━━━━━━━━━━━━━━━━━━━━ 401s 446ms/step - accuracy: 0.5853 - loss: 1.1100 - val_accuracy: 0.5581 - val_loss: 1.1858
Epoch 3/15
898/898 ━━━━━━━━━━━━━━━━━━━━ 364s 406ms/step - accuracy: 0.6083 - loss: 1.0484 - val_accuracy: 0.5744 - val_loss: 1.1351
Epoch 4/15
898/898 ━━━━━━━━━━━━━━━━━━━━ 250s 278ms/step - accuracy: 0.6367 - loss: 0.9819 - val_accuracy: 0.5970 - val_loss: 1.0901
Epoch 5/15
898/898 ━━━━━━━━━━━━━━━━━━━━ 531s 592ms/step - accuracy: 0.6595 - loss: 0.9183 - val_accuracy: 0.5768 - val_loss: 1.1811
Epoch 6/15
898/898 ━━━━━━━━━━━━━━━━━━━━ 445s 496ms/step - accuracy: 0.6979 - loss: 0.8297 - val_accuracy: 0.6188 - val_loss: 1.0997
Epoch 7/15
898/898 ━━━━━━━━━━━━━━━━━━━━ 460s 512ms/step - accuracy: 0.7221 - loss: 0.7651 - val_accuracy: 0.6278 - val_loss: 1.1372
Epoch 8/15
898/898 ━━━━━━━━━━━━━━━━━━━━ 483s 538ms/step - accuracy: 0.7537 -

Deuxième modèle avec des hyperparamètres différents.

In [ ]:

# Construction du modèle CNN
model = models.Sequential([
    layers.Conv2D(64, (3, 3), activation='relu', input_shape=(48, 48, 1)),
    layers.MaxPooling2D(2, 2),
    layers.Conv2D(128, (3, 3), activation='relu'),
    layers.MaxPooling2D(2, 2),
    layers.Conv2D(128, (3, 3), activation='relu'),
    layers.MaxPooling2D(2, 2),
    layers.Flatten(),
    layers.Dense(512, activation='relu'),
    layers.Dense(7, activation='softmax') 
])

model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])


# Utilise un générateur d'images pour pré-traiter et augmenter les données
datagen = ImageDataGenerator(rescale=1./255, validation_split=0.2)
train_data = datagen.flow_from_directory('./fer2013/train', subset='training', target_size=(48, 48), color_mode='grayscale', batch_size=32)
val_data = datagen.flow_from_directory('./fer2013/test', subset='validation', target_size=(48, 48), color_mode='grayscale', batch_size=32)

# Entraîner le modèle
model.fit(train_data, validation_data=val_data, epochs=50)


C:\Users\lea\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\keras\src\layers\convolutional\base_conv.py:107: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(activity_regularizer=activity_regularizer, **kwargs)


Found 22968 images belonging to 7 classes.
Found 1432 images belonging to 7 classes.
Epoch 1/50


C:\Users\lea\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.11_qbz5n2kfra8p0\LocalCache\local-packages\Python311\site-packages\keras\src\trainers\data_adapters\py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


718/718 ━━━━━━━━━━━━━━━━━━━━ 50s 67ms/step - accuracy: 0.2742 - loss: 1.7607 - val_accuracy: 0.4141 - val_loss: 1.4768
Epoch 2/50
718/718 ━━━━━━━━━━━━━━━━━━━━ 46s 64ms/step - accuracy: 0.4546 - loss: 1.4241 - val_accuracy: 0.4749 - val_loss: 1.3602
Epoch 3/50
718/718 ━━━━━━━━━━━━━━━━━━━━ 40s 56ms/step - accuracy: 0.5173 - loss: 1.2627 - val_accuracy: 0.5147 - val_loss: 1.2598
Epoch 4/50
718/718 ━━━━━━━━━━━━━━━━━━━━ 47s 66ms/step - accuracy: 0.5500 - loss: 1.1809 - val_accuracy: 0.5447 - val_loss: 1.2029
Epoch 5/50
718/718 ━━━━━━━━━━━━━━━━━━━━ 65s 90ms/step - accuracy: 0.5866 - loss: 1.0949 - val_accuracy: 0.5545 - val_loss: 1.1843
Epoch 6/50
718/718 ━━━━━━━━━━━━━━━━━━━━ 62s 86ms/step - accuracy: 0.6266 - loss: 0.9974 - val_accuracy: 0.5552 - val_loss: 1.1812
Epoch 7/50
718/718 ━━━━━━━━━━━━━━━━━━━━ 51s 72ms/step - accuracy: 0.6638 - loss: 0.9002 - val_accuracy: 0.5524 - val_loss: 1.1974
Epoch 8/50
718/718 ━━━━━━━━━━━━━━━━━━━━ 52s 72ms/step - accuracy: 0.7056 - loss: 0.7995 - val_accurac

In [ ]:
# Enregsitrer le modèle
model.save('emotion_recognition_modelbasic50.h5')

In [ ]:
# Evaluer le modèle
loss, accuracy = model.evaluate(val_data)
print("Test Accuracy:", accuracy)
print("Loss:", loss)

45/45 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - accuracy: 0.5166 - loss: 5.3688
Test Accuracy: 0.5405027866363525
Loss: 5.199923992156982


Programme qui permet d'ouvrir la caméra de l'ordinateur et de tester le modèle, c'est à dire de determiner l'émotion du visage.

In [ ]:
import cv2
import numpy as np
from tensorflow.keras.models import load_model
from tensorflow.keras.preprocessing import image

# Charger le modèle
model_best = load_model('emotion_recognition_model15epoche.h5')

# Les classes des 7 émotions
class_names = ['Angry', 'Disgusted', 'Fear', 'Happy', 'Sad', 'Surprise', 'Neutral']

# Charger un modèle (fichier XML) qui permet de détecter des visages dans une image en utilisant l'algorithme des cascades de Haar
face_cascade = cv2.CascadeClassifier(cv2.data.haarcascades + 'haarcascade_frontalface_default.xml')

# Ouvrir la connexion avec la webcam ( 0 est la caméra par défaut)
cap = cv2.VideoCapture(0)

while True:
    # Capture image par image
    ret, frame = cap.read()

    # Converti l'image en niveau de gris pour la détéction 
    gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)

    # Detecte le visage sur l'image
    faces = face_cascade.detectMultiScale(gray, scaleFactor=1.3, minNeighbors=5, minSize=(30, 30))

    for (x, y, w, h) in faces:
        # Extrait la région de l'image
        face_roi = frame[y:y + h, x:x + w]

        # Retailler la taille de l'image à la taille du modèle
        face_image = cv2.resize(face_roi, (48, 48))
        face_image = cv2.cvtColor(face_image, cv2.COLOR_BGR2GRAY)
        face_image = image.img_to_array(face_image)
        face_image = np.expand_dims(face_image, axis=0)
        face_image = np.vstack([face_image])

        # Predire l'émotion
        predictions = model_best.predict(face_image)
        emotion_label = class_names[np.argmax(predictions)]

        # Afficher l'émotion
        cv2.putText(frame, f'Emotion: {emotion_label}', (x, y - 10), cv2.FONT_HERSHEY_SIMPLEX,
                    0.9, (0, 0, 255), 2)

        # Dessiner un rectangle autour du visage 
        cv2.rectangle(frame, (x, y), (x + w, y + h), (0, 0, 255), 2)

    # Afficher le résultat
    cv2.imshow('Emotion Detection', frame)

    # Pour sortir de la boucle, pressez 'q'
    if cv2.waitKey(1) & 0xFF == ord('q'):
        break

# Ferme la connexion avec la caméra et ferme la fenêtre 
cap.release()
cv2.destroyAllWindows()



Fonction de test des modèles: 

In [ ]:


# Charger le modèle sauvegardé (.h5)
model = load_model('emotion_recognition_model.h5')

# Fonction pour prétraiter les images du jeu de données de test
def preprocess_image(img_path, target_size=(48, 48)):
    img = image.load_img(img_path, target_size=target_size, color_mode='grayscale')  
    img_array = img_to_array(img) 
    img_array = img_array / 255.0  
    img_array = np.expand_dims(img_array, axis=0) 
    return img_array

# Liste des noms de classes
class_names = ['angry', 'disgust', 'fear', 'happy','neutral', 'sad',  'surprise']

# Fonction pour tester le modèle sur un dataset
def test_model(test_data_dir):
    correct_predictions = 0
    total_predictions = 0
    
    for class_name in os.listdir(test_data_dir): 
        class_dir = os.path.join(test_data_dir, class_name)
        
        for img_name in os.listdir(class_dir):  
            img_path = os.path.join(class_dir, img_name)
            img_array = preprocess_image(img_path)
            
            # Prédiction avec le modèle
            prediction = model.predict(img_array)
            predicted_class = np.argmax(prediction)  
             # Convertir l'indice en nom de classe
            predicted_class_name = class_names[predicted_class]
            
            # Comparer avec la classe réelle
            if predicted_class_name == (class_name): 
                correct_predictions += 1
            total_predictions += 1
    
    # Calculer la précision
    accuracy = correct_predictions / total_predictions
    print(f"Précision : {accuracy:.4f} ({correct_predictions}/{total_predictions} images correctes)")


test_data_dir = 'fer2013/test'
test_model(test_data_dir)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 373ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 67ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 89ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 72ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 80ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 80ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 136ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 68ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 64ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 66ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 81ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 70ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 79ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 62ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 90ms/step
1/1 ━━━━━━

In [ ]:

# Charger le modèle sauvegardé (.h5)
model = load_model('emotion_recognition_model5epoche.h5')

# Fonction pour prétraiter les images du jeu de données de test
def preprocess_image(img_path, target_size=(48, 48)):
    img = image.load_img(img_path, target_size=target_size, color_mode='grayscale')  
    img_array = img_to_array(img)  
    img_array = img_array / 255.0  
    img_array = np.expand_dims(img_array, axis=0)  
    return img_array

#Liste des noms de classes
class_names = ['angry', 'disgust', 'fear', 'happy', 'neutral', 'sad', 'surprise']

# Fonction pour tester le modèle sur un dataset
def test_model(test_data_dir):
    correct_predictions = 0
    total_predictions = 0
    
    for class_name in os.listdir(test_data_dir): 
        class_dir = os.path.join(test_data_dir, class_name)
        
        for img_name in os.listdir(class_dir): 
            img_path = os.path.join(class_dir, img_name)
            img_array = preprocess_image(img_path)
            
            # Prédiction avec le modèle
            prediction = model.predict(img_array)
            predicted_class = np.argmax(prediction)  
             # Convertir l'indice en nom de classe
            predicted_class_name = class_names[predicted_class]
            
            # Comparer avec la classe réelle
            if predicted_class_name == (class_name): 
                correct_predictions += 1
            total_predictions += 1
    
    # Calculer la précision
    accuracy = correct_predictions / total_predictions
    print(f"Précision : {accuracy:.4f} ({correct_predictions}/{total_predictions} images correctes)")

test_data_dir = 'fer2013/test'
test_model(test_data_dir)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 306ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 52ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 61ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 51ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 55ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━

In [ ]:
# Charger le modèle sauvegardé (.h5)
model = load_model('emotion_recognition_model15epoche.h5')

# Fonction pour prétraiter les images du jeu de données de test
def preprocess_image(img_path, target_size=(48, 48)):
    img = image.load_img(img_path, target_size=target_size, color_mode='grayscale')  
    img_array = img_to_array(img) 
    img_array = img_array / 255.0  
    img_array = np.expand_dims(img_array, axis=0) 
    return img_array

#Liste des noms de classes
class_names = ['angry', 'disgust', 'fear', 'happy','neutral', 'sad', 'surprise' ]

# Fonction pour tester le modèle sur un dataset
def test_model(test_data_dir):
    correct_predictions = 0
    total_predictions = 0
    
    for class_name in os.listdir(test_data_dir): 
        class_dir = os.path.join(test_data_dir, class_name)
        
        for img_name in os.listdir(class_dir): 
            img_path = os.path.join(class_dir, img_name)
            img_array = preprocess_image(img_path)
            
            # Prédiction avec le modèle
            prediction = model.predict(img_array)
            predicted_class = np.argmax(prediction)  
             # Convertir l'indice en nom de classe
            predicted_class_name = class_names[predicted_class]
            
            # Comparer avec la classe réelle
            if predicted_class_name == (class_name):  
                correct_predictions += 1
            total_predictions += 1
    
    # Calculer la précision
    accuracy = correct_predictions / total_predictions
    print(f"Précision : {accuracy:.4f} ({correct_predictions}/{total_predictions} images correctes)")

test_data_dir = 'fer2013/test'
test_model(test_data_dir)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 196ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 39ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━

In [ ]:
# Charger le modèle sauvegardé (.h5)
model = load_model('emotion_recognition_model.h5')

# Fonction pour prétraiter les images du jeu de données de test
def preprocess_image(img_path, target_size=(48, 48)):
    img = image.load_img(img_path, target_size=target_size, color_mode='grayscale')  
    img_array = img_to_array(img) 
    img_array = img_array / 255.0  
    img_array = np.expand_dims(img_array, axis=0)
    return img_array

#Liste des noms de classes
class_names = ['angry', 'disgust', 'fear', 'happy','neutral', 'sad', 'surprise' ]

# Fonction pour tester le modèle sur un dataset
def test_model(test_data_dir):
    correct_predictions = 0
    total_predictions = 0
    
    for class_name in os.listdir(test_data_dir): 
        class_dir = os.path.join(test_data_dir, class_name)
        
        for img_name in os.listdir(class_dir):  
            img_path = os.path.join(class_dir, img_name)
            img_array = preprocess_image(img_path)
            
            # Prédiction avec le modèle
            prediction = model.predict(img_array)
            predicted_class = np.argmax(prediction)  
            predicted_class_name = class_names[predicted_class]
            
            # Comparer avec la classe réelle
            if predicted_class_name == (class_name):  
                correct_predictions += 1
            total_predictions += 1
    
    # Calculer la précision
    accuracy = correct_predictions / total_predictions
    print(f"Précision : {accuracy:.4f} ({correct_predictions}/{total_predictions} images correctes)")


test_data_dir = 'fer2013/test'
test_model(test_data_dir)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 80ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━

In [ ]:
# Charger le modèle sauvegardé (.h5)
model = load_model('emotion_recognition_modelbasic15.h5')

# Fonction pour prétraiter les images du jeu de données de test
def preprocess_image(img_path, target_size=(48, 48)):
    img = image.load_img(img_path, target_size=target_size, color_mode='grayscale')  
    img_array = img_to_array(img)  
    img_array = img_array / 255.0  
    img_array = np.expand_dims(img_array, axis=0) 
    return img_array

#Liste des noms de classes
class_names = ['angry', 'disgust', 'fear', 'happy','neutral', 'sad', 'surprise' ]

# Fonction pour tester le modèle sur un dataset
def test_model(test_data_dir):
    correct_predictions = 0
    total_predictions = 0
    
    for class_name in os.listdir(test_data_dir): 
        class_dir = os.path.join(test_data_dir, class_name)
        
        for img_name in os.listdir(class_dir): 
            img_path = os.path.join(class_dir, img_name)
            img_array = preprocess_image(img_path)
            
            # Prédiction avec le modèle
            prediction = model.predict(img_array)
            predicted_class = np.argmax(prediction) 
            predicted_class_name = class_names[predicted_class]
            
            # Comparer avec la classe réelle
            if predicted_class_name == (class_name): 
                correct_predictions += 1
            total_predictions += 1
    
    # Calculer la précision
    accuracy = correct_predictions / total_predictions
    print(f"Précision : {accuracy:.4f} ({correct_predictions}/{total_predictions} images correctes)")

test_data_dir = 'fer2013/test'
test_model(test_data_dir)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 81ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 54ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 37ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 40ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 41ms/step
1/1 ━━━━━━━━

In [ ]:
# Charger le modèle sauvegardé (.h5)
model = load_model('emotion_recognition_modelbasic50.h5')

# Fonction pour prétraiter les images du jeu de données de test
def preprocess_image(img_path, target_size=(48, 48)):
    img = image.load_img(img_path, target_size=target_size, color_mode='grayscale')  
    img_array = img_to_array(img) 
    img_array = img_array / 255.0  
    img_array = np.expand_dims(img_array, axis=0)  
    return img_array

#Liste des noms de classes
class_names = ['angry', 'disgust', 'fear', 'happy','neutral', 'sad', 'surprise' ]

# Fonction pour tester le modèle sur un dataset
def test_model(test_data_dir):
    correct_predictions = 0
    total_predictions = 0
    
    for class_name in os.listdir(test_data_dir):  
        class_dir = os.path.join(test_data_dir, class_name)
        
        for img_name in os.listdir(class_dir):  
            img_path = os.path.join(class_dir, img_name)
            img_array = preprocess_image(img_path)
            
            # Prédiction avec le modèle
            prediction = model.predict(img_array)
            predicted_class = np.argmax(prediction)  
            predicted_class_name = class_names[predicted_class]
            
            # Comparer avec la classe réelle
            if predicted_class_name == (class_name):  
                correct_predictions += 1
            total_predictions += 1
    
    # Calculer la précision
    accuracy = correct_predictions / total_predictions
    print(f"Précision : {accuracy:.4f} ({correct_predictions}/{total_predictions} images correctes)")

test_data_dir = 'fer2013/test'
test_model(test_data_dir)


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 83ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 42ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 30ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 29ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 33ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 36ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 38ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 34ms/step
1/1 ━━━━━━━━

Au vu des résultats et du dataset de base, je pense pas pouvoir faire un modèle plus performant. 